In [1]:
import os, sys
module_path = os.path.abspath(os.path.join('..'))
if module_path not in sys.path:
    sys.path.append(module_path)
from utils.helpers import launch_env, wrap_env, view_results_ipython, change_exercise, seedall, force_done, evaluate_policy
from utils.helpers import SteeringToWheelVelWrapper, ResizeWrapper, ImgWrapper

import numpy as np

import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.autograd import Variable

INFO:aido-protocols:aido-protocols 5.0.5
02:06:18|zn|__init__.py:6|<module>(): zn 2.0.3
02:06:19|zj|__init__.py:5|<module>(): zj 2.0.4
02:06:19|gym-duckietown|__init__.py:10|<module>(): gym-duckietown 2019.0.0

02:06:19|gym-duckietown|__init__.py:24|reg_map_env(): Registering gym environment id: Duckietown-udem1-v0
02:06:19|gym-duckietown|__init__.py:24|reg_map_env(): Registering gym environment id: Duckietown-loop_dyn_duckiebots-v0
02:06:19|gym-duckietown|__init__.py:24|reg_map_env(): Registering gym environment id: Duckietown-4way-v0
02:06:19|gym-duckietown|__init__.py:24|reg_map_env(): Registering gym environment id: Duckietown-loop_pedestrians-v0
02:06:19|gym-duckietown|__init__.py:24|reg_map_env(): Registering gym environment id: Duckietown-zigzag_dists-v0
02:06:19|gym-duckietown|__init__.py:24|reg_map_env(): Registering gym environment id: Duckietown-small_loop_cw-v0
02:06:19|gym-duckietown|__init__.py:24|reg_map_env(): Registering gym environment id: Duckietown-loop_obstacles-v0

# Reinforcement Learning Basics

Reinforcement Learning, as we saw in lecture, is the idea of learning a _policy_ in order to maximize future (potentially discounted) rewards. Our policy, similar to the imitation learning network, maps raw image observations to wheel velocities, and at every timestep, receives a _reward_ from the environment. 

Rewards can be sparse (`1` if goal or task is completed, `0` otherwise) or dense; in general, dense rewards make it easier to learn policies, but as we'll see later in this exercise, defining the correct dense reward is an engineering challenge on its own.

Today's reinforcement learning algorithms are often a mix between _value-based_ and _policy-gradient_ algorithms, instances of what is called an _actor-critic_ formulation. Actor-critic methods have had a lot of research done on them in recent years (especially within in the deep reinforcement learning era), and later in this exercise, we shall also rediscover the formulation's original problems and different methods currently used to stabilize learning.

We begin by defining two networks, an `Actor` and `Critic`; in this exercise, we'll be using a deep RL algorithm titled _Deep Deterministic Policy Gradients_. 

In [2]:
class Actor(nn.Module):
    def __init__(self, action_dim, max_action):
        super(Actor, self).__init__()

        # TODO: You'll need to change this!
        flat_size = 31968

        self.relu = nn.ReLU()
        self.tanh = nn.Tanh()

        self.conv1 = nn.Conv2d(3, 32, 8, stride=2)
        self.conv2 = nn.Conv2d(32, 32, 4, stride=2)

        self.bn1 = nn.BatchNorm2d(32)
        self.bn2 = nn.BatchNorm2d(32)

        self.dropout = nn.Dropout(.1)

        self.lin1 = nn.Linear(flat_size, 100)
        self.lin2 = nn.Linear(100, action_dim)

        self.max_action = max_action

    def forward(self, x):
        x = self.bn1(self.relu(self.conv1(x)))
        x = self.bn2(self.relu(self.conv2(x)))
        x = x.view(x.size(0), -1)  # flatten
        x = self.dropout(x)
        x = self.relu(self.lin1(x))

        x = self.lin2(x)
        x = self.max_action * self.tanh(x)
        
        return x
    
class Critic(nn.Module):
    def __init__(self, action_dim, max_action):
        super(Critic, self).__init__()

        # TODO: You'll need to change this!
        flat_size = 31968

        self.relu = nn.ReLU()
        self.tanh = nn.Tanh()

        self.conv1 = nn.Conv2d(3, 32, 8, stride=2)
        self.conv2 = nn.Conv2d(32, 32, 4, stride=2)

        self.bn1 = nn.BatchNorm2d(32)
        self.bn2 = nn.BatchNorm2d(32)

        self.dropout = nn.Dropout(.1)

        self.lin1 = nn.Linear(flat_size + action_dim, 100)
        self.lin2 = nn.Linear(100, action_dim)

        self.max_action = max_action

    def forward(self, obs, action):
        x = self.bn1(self.relu(self.conv1(obs)))
        x = self.bn2(self.relu(self.conv2(x)))
        x = x.view(x.size(0), -1)  # flatten
        x = self.dropout(x)
        x = torch.cat([x, action], 1)
        x = self.relu(self.lin1(x))

        x = self.lin2(x)
        x = self.max_action * self.tanh(x)
        
        return x

## Reward Engineering

In this part of the exercise, we will experiment with the reward formulation. Given the same model, we'll see how the effect of various reward functions changes the final policy trained. 

In the section below, we'll take a look at the reward function implemented in `gym-duckietown` with a slightly modified training loop. Traditionally, we `reset()` the environment to start an episode, and then `step()` the environment forward for a set amount of time, executing a new action. If this sounds a bit odd, especially for roboticists, you're right - in real robotics, most code runs asynchronously. As a result, although `gym-duckietown` runs locally by stopping the environment, the `AIDO` submissions will run asynchronously, executing the same action until a new one is received.

In [45]:
def updated_reward(env):
    # Compute the collision avoidance penalty
    pos, angle, speed = env.cur_pos, env.cur_angle, env.speed
    col_penalty = env.proximity_penalty2(pos, angle)
    # Get the position relative to the right lane tangent
    try:
        lp = env.get_lane_pos2(pos, angle)
    except NotInLane:
        reward = 40 * col_penalty
    else:

        # Compute the reward
        reward = (
                +5000.0 * speed * lp.dot_dir +
                -10 * np.abs(lp.dist) +
                +40 * col_penalty
        )
    return reward

In [46]:
nepisodes = 3

In [43]:
local_env = launch_env()
local_env = wrap_env(local_env)
local_env = ResizeWrapper(local_env)
local_env = ImgWrapper(local_env)

for _ in range(nepisodes):
    done = False
    obs = local_env.reset()
    while not done:
        obs, r, done, info = local_env.step(policy.predict(obs))
        new_r = updated_reward(local_env)
        print(r, new_r)
 

03:04:26|gym-duckietown|graphics.py:121|create_frame_buffers(): Falling back to non-multisampled frame buffer
03:04:26|gym-duckietown|graphics.py:121|create_frame_buffers(): Falling back to non-multisampled frame buffer
03:04:26|gym-duckietown|simulator.py:550|_load_map(): loading map file "/duckietown/simulation/gym_duckietown/maps/loop_empty.yaml"
03:04:26|gym-duckietown|simulator.py:1107|_drivable_pos(): [4.13719561 0.         1.88880899] corresponds to tile at (7, 3) which is not drivable: {'coords': (7, 3), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.gym_duckietown.graphics.Texture object at 0x7f0f87b7f748>, 'color': array([1, 1, 1])}
03:04:26|gym-duckietown|simulator.py:1217|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
03:04:26|gym-duckietown|simulator.py:1218|_valid_pose(): safety_factor: 1.3
03:04:26|gym-duckietown|simulator.py:1219|_valid_pose(): pos: [4.0873995 0.        1.9726338]
03:04:26|gym-duckietown|simulator.py:12

03:04:26|gym-duckietown|simulator.py:1217|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
03:04:26|gym-duckietown|simulator.py:1218|_valid_pose(): safety_factor: 1.3
03:04:26|gym-duckietown|simulator.py:1219|_valid_pose(): pos: [3.57292165 0.         1.88314807]
03:04:26|gym-duckietown|simulator.py:1220|_valid_pose(): l_pos: [3.48172154 0.         1.84866924]
03:04:26|gym-duckietown|simulator.py:1221|_valid_pose(): r_pos: [3.66412176 0.         1.91762689]
03:04:26|gym-duckietown|simulator.py:1222|_valid_pose(): f_pos: [3.61429624 0.         1.77370793]
03:04:26|gym-duckietown|simulator.py:1107|_drivable_pos(): [3.50690495 0.         2.23654429] corresponds to tile at (5, 3) which is not drivable: {'coords': (5, 3), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.gym_duckietown.graphics.Texture object at 0x7f0f87b7f748>, 'color': array([1, 1, 1])}
03:04:26|gym-duckietown|simulator.py:1217|_valid_pose(): Invalid pose. Collision free: True

03:04:26|gym-duckietown|simulator.py:1222|_valid_pose(): f_pos: [3.50609039 0.         2.05544313]
03:04:26|gym-duckietown|simulator.py:1107|_drivable_pos(): [4.12972415 0.         2.27350789] corresponds to tile at (7, 3) which is not drivable: {'coords': (7, 3), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.gym_duckietown.graphics.Texture object at 0x7f0f87b7f748>, 'color': array([1, 1, 1])}
03:04:26|gym-duckietown|simulator.py:1217|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
03:04:26|gym-duckietown|simulator.py:1218|_valid_pose(): safety_factor: 1.3
03:04:26|gym-duckietown|simulator.py:1219|_valid_pose(): pos: [4.022444   0.         2.32019802]
03:04:26|gym-duckietown|simulator.py:1220|_valid_pose(): l_pos: [3.98353555 0.         2.23079789]
03:04:26|gym-duckietown|simulator.py:1221|_valid_pose(): r_pos: [4.06135244 0.         2.40959815]
03:04:26|gym-duckietown|simulator.py:1222|_valid_pose(): f_pos: [4.12972415 0.         2.27

03:04:30|gym-duckietown|simulator.py:1107|_drivable_pos(): [2.28873639 0.         2.68406941] corresponds to tile at (3, 4) which is not drivable: {'coords': (3, 4), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.gym_duckietown.graphics.Texture object at 0x7f0f87b7f748>, 'color': array([1, 1, 1])}
03:04:30|gym-duckietown|simulator.py:1217|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
03:04:30|gym-duckietown|simulator.py:1218|_valid_pose(): safety_factor: 1.3
03:04:30|gym-duckietown|simulator.py:1219|_valid_pose(): pos: [2.38071712 0.         2.71640816]
03:04:30|gym-duckietown|simulator.py:1220|_valid_pose(): l_pos: [2.28873639 0.         2.68406941]
03:04:30|gym-duckietown|simulator.py:1221|_valid_pose(): r_pos: [2.47269785 0.         2.74874692]
03:04:30|gym-duckietown|simulator.py:1222|_valid_pose(): f_pos: [2.41952363 0.         2.60603129]
03:04:30|gym-duckietown|simulator.py:531|reset(): Starting at [2.64153703 0.         2.8846

-0.11008460519299601 1.3100253097773256
-0.11008460519299601 1.3100253097773256
-0.11008460519299601 1.3100253097773256
-0.11008460519299601 1.3100253097773256


...

-2.4424800727876703 3.3927284936164215
-2.440324499047021 3.4064204564026968
-2.4377593388954133 3.418734269559156
-2.4322741785660265 3.428644405625607
-2.424897746072933 3.436261752752312
-2.4168214030204513 3.4413789141189532
-2.4084749937661076 3.4459325252770823


03:05:39|gym-duckietown|simulator.py:1435|_render_img(): Pos: [3.574416164158833, 0, 2.216129092780792] angle 2.058192127362198
03:05:39|gym-duckietown|simulator.py:1435|_render_img(): Pos: [3.574351550842229, 0, 2.2160047563934517] angle 2.041912251313597
03:05:39|gym-duckietown|simulator.py:1435|_render_img(): Pos: [3.574467360635135, 0, 2.2162366804272864] angle 2.025925179953574
03:05:39|gym-duckietown|simulator.py:1435|_render_img(): Pos: [3.574550877399056, 0, 2.2164113907854155] angle 2.0075024868703317
03:05:39|gym-duckietown|simulator.py:1435|_render_img(): Pos: [3.57452605207096, 0, 2.216356967513157] angle 1.990007771432759
03:05:39|gym-duckietown|simulator.py:1435|_render_img(): Pos: [3.574443641921151, 0, 2.2161676010038462] angle 1.972522386594979
03:05:39|gym-duckietown|simulator.py:1435|_render_img(): Pos: [3.574273161572795, 0, 2.215757535183028] angle 1.957071085512148


-2.3993611834266213 3.448928767822532
-2.3905717956466175 3.4508383584116675
-2.3822096760647398 3.4514844915777054
-2.3724811201112614 3.4503263936486483
-2.3621115510834083 3.449491226009438
-2.3536472415914615 3.449739479290397
-2.3460986252598994 3.4505635807884882


03:05:39|gym-duckietown|simulator.py:1435|_render_img(): Pos: [3.5739759135921445, 0, 2.215010708726232] angle 1.942109217316535
03:05:39|gym-duckietown|simulator.py:1435|_render_img(): Pos: [3.5735811836183937, 0, 2.2139732457947385] angle 1.9266095846097646
03:05:39|gym-duckietown|simulator.py:1435|_render_img(): Pos: [3.5731920399716803, 0, 2.2129062160500097] angle 1.9143997900561054
03:05:39|gym-duckietown|simulator.py:1435|_render_img(): Pos: [3.572791578970606, 0, 2.2117670629725756] angle 1.903289947076989
03:05:39|gym-duckietown|simulator.py:1107|_drivable_pos(): [3.50973285 0.         2.2589327 ] corresponds to tile at (5, 3) which is not drivable: {'coords': (5, 3), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.gym_duckietown.graphics.Texture object at 0x7f0f87b7f748>, 'color': array([1, 1, 1])}
03:05:39|gym-duckietown|simulator.py:1217|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
03:05:39|gym-duckietown|simulator.py:1218

-2.3406856652825194 3.452268384272048
-2.337018727176482 3.4552408640785526
-2.334351965981545 3.4591881638160604
-2.333223393673837 3.4630796002831943
-1000 3.4670842102939403


In [44]:
view_results_ipython(local_env)

**Question 0: After understanding the above computed reward, experiment with the constants for each component. What type of behavior does the above reward function penalize? Is this good or bad in context of autonomous driving? Name some other issues that can arise with single-objective optimization. In addition, give three sets of constants and explain qualitatively what types of behavior each penalizes or rewards (note, you may want to use a different action policy than random)**. Place the answers to the above in `reinforcement-learning-answers.txt`




# The Reinforcement Learning Learning Code

Below we'll see a relatively naive implementation of the actor-critic training loop, which proceeds as follows: the critic is tasked with a supervised learning problem of fitting rewards acquired by the agent. Then, the policy, using policy gradients, maximizes the return according to the critic's estimate, rather than using Monte-Carlo updates.

Below, we see an implementation of `DDPGAgent`, a class which handles the networks and training loop. 

In [35]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

class DDPGAgent(object):
    def __init__(self, state_dim, action_dim, max_action=1.0):
        super(DDPGAgent, self).__init__()

        self.actor = Actor(action_dim, max_action).to(device)
        self.actor_optimizer = torch.optim.Adam(self.actor.parameters(), lr=5e-2)
        
        self.critic = Critic(action_dim, max_action).to(device)
        self.critic_optimizer = torch.optim.Adam(self.critic.parameters(), lr=5e-2)

    def predict(self, state):
        assert state.shape[0] == 3
        state = torch.FloatTensor(np.expand_dims(state, axis=0)).to(device)
        return self.actor(state).cpu().data.numpy().flatten()

    def train(self, replay_buffer, iterations, batch_size=64, discount=0.99):
        for it in range(iterations):

            # Sample replay buffer
            sample = replay_buffer.sample(batch_size)
            state = torch.FloatTensor(sample["state"]).to(device)
            action = torch.FloatTensor(sample["action"]).to(device)
            next_state = torch.FloatTensor(sample["next_state"]).to(device)
            done = torch.FloatTensor(1 - sample["done"]).to(device)
            reward = torch.FloatTensor(sample["reward"]).to(device)

            # Compute the target Q value
            target_Q = self.critic(next_state, self.actor(next_state))
            
            # TODO: - no detach is a subtle, but important bug!
            target_Q = reward + (done * discount * target_Q.detach())

            # Get current Q estimate
            current_Q = self.critic(state, action)

            # Compute critic loss
            critic_loss = F.mse_loss(current_Q, target_Q)

            # Optimize the critic
            self.critic_optimizer.zero_grad()
            critic_loss.backward()
            self.critic_optimizer.step()

            # Compute actor loss
            actor_loss = -self.critic(state, self.actor(state)).mean()

            # Optimize the actor
            self.actor_optimizer.zero_grad()
            actor_loss.backward()
            self.actor_optimizer.step()
            
    def save(self, filename, directory):
        torch.save(self.actor.state_dict(), '{}/{}_actor.pth'.format(directory, filename))
        torch.save(self.critic.state_dict(), '{}/{}_critic.pth'.format(directory, filename))

    def load(self, filename, directory):
        self.actor.load_state_dict(torch.load('{}/{}_actor.pth'.format(directory, filename), map_location=device))
        self.critic.load_state_dict(torch.load('{}/{}_critic.pth'.format(directory, filename), map_location=device))


You'll notice that the training loop needs a `replay_buffer` object. In value-based and actor-critic methods in deep reinforcement learning, the use of a replay buffer is crucial. In the following sections, you'll explore why this is the case, and some other stabilization techniques that are needed in order to get the above code to work. Below, you can find an implementation of the replay buffer, as well the training loop that we use to train DDPG.

In [36]:
# Simple replay buffer
class ReplayBuffer(object):
    def __init__(self, max_size=1e6):
        self.storage = []
        self.max_size = max_size

    # Expects tuples of (state, next_state, action, reward, done)
    def add(self, state, next_state, action, reward, done):
        if len(self.storage) < self.max_size:
            self.storage.append((state, next_state, action, reward, done))
        else:
            # Remove random element in the memory before adding a new one
            self.storage.pop(random.randrange(len(self.storage)))
            self.storage.append((state, next_state, action, reward, done))


    def sample(self, batch_size=100, flat=False):
        ind = np.random.randint(0, len(self.storage), size=batch_size)
        states, next_states, actions, rewards, dones = [], [], [], [], []

        for i in ind:
            state, next_state, action, reward, done = self.storage[i]

            if flat:
                states.append(np.array(state, copy=False).flatten())
                next_states.append(np.array(next_state, copy=False).flatten())
            else:
                states.append(np.array(state, copy=False))
                next_states.append(np.array(next_state, copy=False))
            actions.append(np.array(action, copy=False))
            rewards.append(np.array(reward, copy=False))
            dones.append(np.array(done, copy=False))

        # state_sample, action_sample, next_state_sample, reward_sample, done_sample
        return {
            "state": np.stack(states),
            "next_state": np.stack(next_states),
            "action": np.stack(actions),
            "reward": np.stack(rewards).reshape(-1,1),
            "done": np.stack(dones).reshape(-1,1)
        }

In [37]:
seed_ = 123
max_timesteps = 500 
batch_size = 64
discount = 0.99
eval_freq = 5e3
file_name = 'dt-class-rl'
start_timesteps = 1e4
expl_noise = 0.1

In [47]:
import os

local_env = launch_env()
# local_env = wrap_env(local_env)
local_env = ResizeWrapper(local_env)
local_env = ImgWrapper(local_env)

if not os.path.exists("./pytorch_models"):
    os.makedirs("./pytorch_models")

# Set seeds
seedall(seed_)

state_dim = local_env.observation_space.shape
action_dim = local_env.action_space.shape[0]
max_action = float(local_env.action_space.high[0])

# Initialize policy
policy = DDPGAgent(state_dim, action_dim, max_action)

replay_buffer = ReplayBuffer()

# Evaluate untrained policy
evaluations= [evaluate_policy(local_env, policy)]

total_timesteps = 0
timesteps_since_eval = 0
episode_num = 0
done = True
episode_reward = None
env_counter = 0
while total_timesteps < max_timesteps:
    if done:
        if total_timesteps != 0:
            print(("Total T: %d Episode Num: %d Episode T: %d Reward: %f") % (
                total_timesteps, episode_num, episode_timesteps, episode_reward))
            policy.train(replay_buffer, episode_timesteps, batch_size, discount)

        # Evaluate episode
        if timesteps_since_eval >= eval_freq:
            timesteps_since_eval %= eval_freq
            evaluations.append(evaluate_policy(local_env, policy))

            policy.save(file_name, directory="./pytorch_models")
            np.savez("./pytorch_models/{}.npz".format(file_name),evaluations)

        # Reset environment
        env_counter += 1
        obs = local_env.reset()
        done = False
        episode_reward = 0
        episode_timesteps = 0
        episode_num += 1

    # Select action randomly or according to policy
    if total_timesteps < start_timesteps:
        action = local_env.action_space.sample()
    else:
        action = policy.predict(np.array(obs))
        if expl_noise != 0:
            action = (action + np.random.normal(
                0,
                expl_noise,
                size=local_env.action_space.shape[0])
            ).clip(-1, +1)

    # Perform action
    new_obs, reward, done, _ = local_env.step(action)
    reward = updated_reward(local_env)

    if episode_timesteps >= max_timesteps:
        done = True

    done_bool = 0 if episode_timesteps + 1 == max_timesteps else float(done)
    episode_reward += reward

    # Store data in replay buffer
    replay_buffer.add(obs, new_obs, action, reward, done_bool)

    obs = new_obs

    episode_timesteps += 1
    total_timesteps += 1
    timesteps_since_eval += 1

# Final evaluation
evaluations.append(evaluate_policy(local_env, policy))

policy.save(file_name, directory="./pytorch_models")
np.savez("./pytorch_models/{}.npz".format(file_name),evaluations)

03:07:15|gym-duckietown|graphics.py:121|create_frame_buffers(): Falling back to non-multisampled frame buffer
03:07:15|gym-duckietown|graphics.py:121|create_frame_buffers(): Falling back to non-multisampled frame buffer
03:07:15|gym-duckietown|simulator.py:550|_load_map(): loading map file "/duckietown/simulation/gym_duckietown/maps/loop_empty.yaml"
03:07:15|gym-duckietown|simulator.py:1107|_drivable_pos(): [4.13719561 0.         1.88880899] corresponds to tile at (7, 3) which is not drivable: {'coords': (7, 3), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.gym_duckietown.graphics.Texture object at 0x7f0f87b7f748>, 'color': array([1, 1, 1])}
03:07:15|gym-duckietown|simulator.py:1217|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
03:07:15|gym-duckietown|simulator.py:1218|_valid_pose(): safety_factor: 1.3
03:07:15|gym-duckietown|simulator.py:1219|_valid_pose(): pos: [4.0873995 0.        1.9726338]
03:07:15|gym-duckietown|simulator.py:12

03:07:15|gym-duckietown|simulator.py:1217|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
03:07:15|gym-duckietown|simulator.py:1218|_valid_pose(): safety_factor: 1.3
03:07:15|gym-duckietown|simulator.py:1219|_valid_pose(): pos: [3.57292165 0.         1.88314807]
03:07:15|gym-duckietown|simulator.py:1220|_valid_pose(): l_pos: [3.48172154 0.         1.84866924]
03:07:15|gym-duckietown|simulator.py:1221|_valid_pose(): r_pos: [3.66412176 0.         1.91762689]
03:07:15|gym-duckietown|simulator.py:1222|_valid_pose(): f_pos: [3.61429624 0.         1.77370793]
03:07:15|gym-duckietown|simulator.py:1107|_drivable_pos(): [3.50690495 0.         2.23654429] corresponds to tile at (5, 3) which is not drivable: {'coords': (5, 3), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.gym_duckietown.graphics.Texture object at 0x7f0f87b7f748>, 'color': array([1, 1, 1])}
03:07:15|gym-duckietown|simulator.py:1217|_valid_pose(): Invalid pose. Collision free: True

03:07:15|gym-duckietown|simulator.py:1222|_valid_pose(): f_pos: [3.50609039 0.         2.05544313]
03:07:15|gym-duckietown|simulator.py:1107|_drivable_pos(): [4.12972415 0.         2.27350789] corresponds to tile at (7, 3) which is not drivable: {'coords': (7, 3), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.gym_duckietown.graphics.Texture object at 0x7f0f87b7f748>, 'color': array([1, 1, 1])}
03:07:15|gym-duckietown|simulator.py:1217|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
03:07:15|gym-duckietown|simulator.py:1218|_valid_pose(): safety_factor: 1.3
03:07:15|gym-duckietown|simulator.py:1219|_valid_pose(): pos: [4.022444   0.         2.32019802]
03:07:15|gym-duckietown|simulator.py:1220|_valid_pose(): l_pos: [3.98353555 0.         2.23079789]
03:07:15|gym-duckietown|simulator.py:1221|_valid_pose(): r_pos: [4.06135244 0.         2.40959815]
03:07:15|gym-duckietown|simulator.py:1222|_valid_pose(): f_pos: [4.12972415 0.         2.27

03:07:20|gym-duckietown|simulator.py:1217|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
03:07:20|gym-duckietown|simulator.py:1218|_valid_pose(): safety_factor: 1.3
03:07:20|gym-duckietown|simulator.py:1219|_valid_pose(): pos: [2.38071712 0.         2.71640816]
03:07:20|gym-duckietown|simulator.py:1220|_valid_pose(): l_pos: [2.28873639 0.         2.68406941]
03:07:20|gym-duckietown|simulator.py:1221|_valid_pose(): r_pos: [2.47269785 0.         2.74874692]
03:07:20|gym-duckietown|simulator.py:1222|_valid_pose(): f_pos: [2.41952363 0.         2.60603129]
03:07:20|gym-duckietown|simulator.py:531|reset(): Starting at [2.64153703 0.         2.88468928] 4.836049502872963
03:07:20|gym-duckietown|simulator.py:1435|_render_img(): Pos: [2.64153703 0.         2.88468928] angle 4.836049502872963
03:07:20|gym-duckietown|simulator.py:1435|_render_img(): Pos: [2.6415370304316736, 0, 2.884689280745409] angle -1.4471358043066236
03:07:20|gym-duckietown|simulator.py:1435|_rend

03:07:21|gym-duckietown|simulator.py:1435|_render_img(): Pos: [2.6367627913545837, 0, 2.946564887177869] angle -1.8524532234403686
03:07:21|gym-duckietown|simulator.py:1435|_render_img(): Pos: [2.636555929148821, 0, 2.9472603903236005] angle -1.8673306727174255
03:07:21|gym-duckietown|simulator.py:1435|_render_img(): Pos: [2.6362173492687666, 0, 2.9483428789389565] angle -1.880540324984933
03:07:21|gym-duckietown|simulator.py:1435|_render_img(): Pos: [2.6358490839570807, 0, 2.94947315725907] angle -1.890995940714123
03:07:21|gym-duckietown|simulator.py:1435|_render_img(): Pos: [2.6353824117821847, 0, 2.950863993233157] angle -1.898055649743603
03:07:21|gym-duckietown|simulator.py:1435|_render_img(): Pos: [2.634839916588329, 0, 2.952444602121065] angle -1.9047794483720586
03:07:21|gym-duckietown|simulator.py:1435|_render_img(): Pos: [2.6342849262151353, 0, 2.9540344389936832] angle -1.908534521214463
03:07:21|gym-duckietown|simulator.py:1435|_render_img(): Pos: [2.6337065921147973, 0, 2

...

03:20:25|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.7456950504409994, 0, 2.3240788304207953] angle -1.545525817519297
03:20:25|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.7457309689875382, 0, 2.325615913146028] angle -1.5493393435852751
03:20:25|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.7457599921810438, 0, 2.3271269529274985] angle -1.5538431694907855
03:20:25|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.7457804387579215, 0, 2.3285927546651495] angle -1.559853145371691
03:20:25|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.7457908176520335, 0, 2.3299015529204565] angle -1.5658796512625692
03:20:26|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.7457930512901944, 0, 2.3310794694379076] angle -1.5719204831620905
03:20:26|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.7457884106289503, 0, 2.332251612000138] angle -1.577590383018731
03:20:26|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.7457784918113823

03:20:27|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.7342658644836098, 0, 2.3922500700595855] angle -2.1800091676555966
03:20:27|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.7333805385471462, 0, 2.3934981919756666] angle -2.1954994177766762
03:20:27|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.7323581973723132, 0, 2.39489136546295] angle -2.2122261389448563
03:20:27|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.7313152805723235, 0, 2.3962642421160325] angle -2.2286738343675623
03:20:27|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.7303088709685613, 0, 2.3975458450819587] angle -2.2443128355165665
03:20:27|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.7294506576149749, 0, 2.3986036469738554] angle -2.260487729035508
03:20:27|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.7287649916797175, 0, 2.3994216373671087] angle -2.2763499016112028
03:20:27|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.72799198500294

03:20:28|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.681958723697808, 0, 2.424677001314479] angle -2.9268119554606797
03:20:28|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.6813325730496383, 0, 2.4248063957323405] angle -2.948809093975632
03:20:28|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.6807518780593655, 0, 2.4249129400819935] angle -2.9714580988580654
03:20:28|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.6800111755560913, 0, 2.4250308722071736] angle -2.995944585197711
03:20:29|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.6792061486035202, 0, 2.4251382849870793] angle -3.021952503253431
03:20:29|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.6783198343027355, 0, 2.4252335802833853] angle -3.0470184788791626
03:20:29|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.6772898606437137, 0, 2.4253182662932695] angle -3.0720928387036253
03:20:29|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.6763639327226362

03:20:30|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.6656800759004093, 0, 2.42481709353477] angle 2.9543000270158895
03:20:30|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.6657713741238926, 0, 2.424834499111797] angle 2.9521159057901984
03:20:30|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.6657979520937174, 0, 2.4248396141556317] angle 2.9508101288695174
03:20:30|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.6657434349212707, 0, 2.4248290237676224] angle 2.9486387742572973
03:20:30|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.6657679603500736, 0, 2.424833845985143] angle 2.946257442549053
03:20:30|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.6657756699062513, 0, 2.4248353975583026] angle 2.939727249751952
03:20:30|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.6658829145807774, 0, 2.424857979945668] angle 2.928384154634057
03:20:30|gym-duckietown|simulator.py:1435|_render_img(): Pos: [0.6660469693415316, 0, 2.424

03:20:31|gym-duckietown|simulator.py:1376|_compute_done_reward(): Stopping the simulator because we are at an invalid pose.


# Stabilizing DDPG

As you may notice, the above model performs poorly or doesn't converge. Your job is to improve it; first in the notebook, later in the AIDO submission. This last part of the assignment consists of four sections:

**1. There are subtle, but important, bugs that have been introduced into the code above. Your job is to find them, and explain them in your `reinforcement-learning-answers.txt`. You'll want to reread the original [DQN](https://deepmind.com/research/publications/human-level-control-through-deep-reinforcement-learning) and [DDPG](https://arxiv.org/abs/1509.02971) papers in order to better understand the issue, but by answering the following subquestions (*please put the answers to these in the submission for full credit*), you'll be on the right track:**

   a) Read some literature on actor-critic methods, including the original [actor-critic](https://papers.nips.cc/paper/1786-actor-critic-algorithms.pdf) paper. What is an issue that you see related to *non-stationarity*? Define what _non-stationarity_ means in the context of machine learning and how it relates to actor-critic methods. In addition, give some hypotheses on why reinforcement learning is much more difficult (from an optimization perspective) than supervised learning, and how the answer to the previous question and this one are related.

   b) What role does the replay buffer play in off-policy reinforcement learning? It's most important parameter is `max_size` - how does changing this value (answer for both increasing and decreasing trends) qualitatively affect the training of the algorithm?

   c) **Challenge Question:** Briefly, explain how automatic differentiation works. In addition, expand on the difference between a single-element tensor (that `requires_grad`) and a scalar value as it relates to automatic differentiation; when do we want to backpropogate through a single-element tensor, and when do we not? Take a close look at the code and how losses are being backpropogated. On paper or your favorite drawing software, draw out the actor-critic architecture *as described in the code*, and label how the actor and critic losses are backpropogated. On your diagram, highlight the particular loss that will cause issues with the above code, and fix it.
   
For the next section, please pick **either** the theoretical or the practical pathway. If you don't have access to the necessary compute, for the exercise, please do the theoretical portion. 
   
_Theoretical Component_ 

**2. We discussed a case study of DQN in class. The original authors used quite a few tricks to get this to work. Detail some of the following, and explain what problem they solve in training the DQN:**

a) Target Networks

b) Annealed Learning Rates

c) Replay Buffer

d) Random Exploration Period

e) Preprocessing the Image


**3. Read about either [TD3](https://arxiv.org/abs/1802.09477) or [Soft Actor Critic](https://arxiv.org/abs/1801.01290); for your choice, summarize what problems they are addressing with the standard actor-critic formulation, and how they solve them**


_Practical Component_ 

**2. [Optional - if you have access to compute] Using your analysis from the reward engineering ablation, train two agents (after you've found the bugs in DDPG) - one with the standard, `gym-duckietown` reward, and another with the parameters of your choosing. Report each set of parameters, and describe qualitatively what type of behavior the agent produces.**

If you don't have the resources to actually train these agents, instead describe what types of behaviors each reward function might prioritize.

**3. [Optional - if you have access to compute] Using the instructions [here](http://docs.duckietown.org/DT19/AIDO/out/embodied_rl.html), use the saved policy files from this notebook and submit using the template submission provided through the AIDO submission. Report your best submission number (i.e the one you'd like to be graded) in `reinforcement-learning-answers.txt`**